In [1]:
import geopandas as gpd
import pandas as pd
import folium, branca
import fiona, requests, json
import os
import fiona.crs
import requests
import fiona
import numpy as np 
import math

from folium.features import GeoJson, GeoJsonTooltip

In [2]:
# importando os mapas e convertendo em GeoJson
mapa31 = gpd.GeoDataFrame.from_features(requests.get('https://raw.githubusercontent.com/lucasvascrocha/mapa_ternium/master/data/processed/mapa31.json').json(), crs=fiona.crs.from_epsg(4326))
mapa32 = gpd.GeoDataFrame.from_features(requests.get('https://raw.githubusercontent.com/lucasvascrocha/mapa_ternium/master/data/processed/mapa32.json').json(), crs=fiona.crs.from_epsg(4326))
mapa33 = gpd.GeoDataFrame.from_features(requests.get('https://raw.githubusercontent.com/lucasvascrocha/mapa_ternium/master/data/processed/mapa33.json').json(), crs=fiona.crs.from_epsg(4326))
mapa34 = gpd.GeoDataFrame.from_features(requests.get('https://raw.githubusercontent.com/lucasvascrocha/mapa_ternium/master/data/processed/mapa34.json').json(), crs=fiona.crs.from_epsg(4326))

# Juntando os mapas em um GeoDf
allcities = mapa31.append(mapa32, ignore_index=True)
allcities = allcities.append(mapa33, ignore_index=True)
allcities=allcities.append(mapa34, ignore_index=True)

allcities

/home/lucas/.local/lib/python3.6/site-packages/pyproj/crs/crs.py:55: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


In [4]:
# juntando arquivos Json em um DF para retirar apenas os pontos de coordenadas 
for i in range(31,35):
    endND = os.path.join('geojs-'+str(i)+'-mun.json')
    geo_json_ND = json.load(open(endND, encoding='latin-1'))
    
    if i == 31:
        geo_json_NDX = geo_json_ND
        
    else:
         for city in geo_json_ND['features']:
                geo_json_NDX['features'].append(city)                   

In [9]:
# Crinado uma lista com o primeiro valor de latitude e longitude de todas cidades
geometria=[]
for city in geo_json_NDX['features']:
    geometria.append(city['geometry']['coordinates'][0][0]) 

# adicionando colunas float ao GeoDf
allcities['lat']=1.0
allcities['lon']=1.0

In [10]:
# Adicionando latitude e longitude de cada cidade ao GeoDf
for c in range(0,1668):
    allcities['lat'][c] = (geometria[c][0])
    
for c in range(0,1668):
    allcities['lon'][c] = (geometria[c][1])

/home/lucas/.local/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/lucas/.local/lib/python3.6/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [13]:
#Adicionando coluna distancia linha reta 
allcities['distancia_l_reta'] = 1.0

#localizando o ponto de partida (Itaguaí) para usar sua latitude (-43.8289) e lon(-23.057311)
allcities.loc[allcities['name']=='Itaguaí']

geometry       id     name  \
960  POLYGON ((-43.82790 -23.05731, -43.79357 -23.0...  3302007  Itaguaí   

    description      lat        lon  distancia_l_reta  
960     Itaguaí -43.8279 -23.057311               1.0

In [14]:
# Programa para calcular a distância entre duas coordenadas geográficas
from math import radians, cos, sin, asin, sqrt 
def distance(lat1, lat2, lon1, lon2): 
	
	# The math module contains a function named 
	# radians which converts from degrees to radians. 
	lon1 = radians(lon1) 
	lon2 = radians(lon2) 
	lat1 = radians(lat1) 
	lat2 = radians(lat2) 
	
	# Haversine formula 
	dlon = lon2 - lon1 
	dlat = lat2 - lat1 
	a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2

	c = 2 * asin(sqrt(a)) 
	
	# Radius of earth in kilometers. Use 3956 for miles 
	r = 6371
	
	# calculate the result 
	return(f'{c * r:.2f}') 
	
	
# driver code 
lat1 = 53.32055555555556
lat2 = 53.31861111111111
lon1 = -1.7297222222222221
lon2 = -1.6997222222222223
print(distance(lat1, lat2, lon1, lon2), "K.M") 

2.00 K.M


In [15]:
# Adiciona a distancia em linha reta de cada cidade através do programa (distance)
for c in range(0,1668):
    allcities['distancia_l_reta'][c] = distance(-43.8279,allcities['lat'][c], -23.057311, allcities['lon'][c])


/home/lucas/.local/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [17]:
# Cria uma coluna float, distancia realm aproximada
allcities['distancia-real-aprox'] = 1.0

# Aplicação do parâmetro: distância real aproximada é = à distância em linha reta * 1.5
allcities['distancia-real-aprox'] = allcities['distancia_l_reta'].apply(lambda x: x*1.5)

allcities

geometry       id  \
0     POLYGON ((-47.44410 -18.15847, -47.43543 -18.1...  3100104   
1     POLYGON ((-45.18200 -18.88757, -45.17314 -18.8...  3100203   
2     POLYGON ((-42.36955 -20.13218, -42.35755 -20.1...  3100302   
3     POLYGON ((-43.11391 -20.35784, -43.10969 -20.3...  3100401   
4     POLYGON ((-42.38592 -18.92388, -42.38140 -18.9...  3100500   
...                                                 ...      ...   
1663  POLYGON ((-47.37268 -23.51783, -47.37047 -23.5...  3557006   
1664  POLYGON ((-50.02073 -20.33347, -50.01275 -20.3...  3557105   
1665  POLYGON ((-49.99521 -21.03253, -49.98434 -21.0...  3557154   
1666  POLYGON ((-49.68539 -22.94866, -49.68396 -22.9...  3557204   
1667  POLYGON ((-46.91399 -22.19933, -46.91221 -22.2...  3557303   

                     name          description        lat        lon  \
0     Abadia dos Dourados  Abadia dos Dourados -47.444098 -18.158465   
1                  Abaeté               Abaeté -45.182004 -18.887567   
2              Abre Campo           Abre Campo -42.369553 -20.132179   
3                 Acaiaca              Acaiaca -43.113912 -20.357837   
4                 Açucena              Açucena -42.385922 -18.923883   
...                   ...                  ...        ...        ...   
1663           Votorantim           Votorantim -47.372676 -23.517835   
1664          Votuporanga          Votuporanga -50.020735 -20.333469   
1665             Zacarias             Zacarias -49.995211 -21.032526   
1666            Chavantes            Chavantes -49.685393 -22.948660   
1667         Estiva Gerbi         Estiva Gerbi -46.913992 -22.199327   

      distancia_l_reta  distancia-real-aprox  
0               553.64               830.460  
1               363.28               544.920  
2               287.55               431.325  
3               231.84               347.760  
4               371.84               557.760  
...                ...                   ...  
1663            395.78               593.670  
1664            718.88              1078.320  
1665            702.74              1054.110  
1666            651.38               977.070  
1667            349.64               524.460  

[1668 rows x 8 columns]

In [22]:
# Criação do mapa folium
colormap = branca.colormap.LinearColormap(vmin=allcities['distancia-real-aprox'].quantile(0.0), vmax=allcities['distancia-real-aprox'].quantile(1), colors=['green', 'yellow', 'red'])
m = folium.Map(location=[-25.826592, -35.212558], zoom_start=5, tiles='Stamen Terrain')
tooltip = GeoJsonTooltip(fields=['name', 'distancia-real-aprox'], aliases=['Cidade', 'Distância'], localize=True, sticky=False, labels=True, style="""background-color: transparent""")

# Adicionando escala e título
colormap.caption = 'Zona de Alcance (Km)'
colormap.add_to(m)

# Estilo das cores em função da distancia-real-aprox
g = folium.GeoJson(allcities, style_function=lambda x: {"fillColor": colormap(x["properties"]["distancia-real-aprox"])if x["properties"]["distancia-real-aprox"] is not None else "transparent", "color": "transparent", "fillOpacity": 0.4,}, tooltip=tooltip).add_to(m)

In [23]:
m

In [24]:
path='mapsudeste.html'
m.save(path)